## Knowledge graph experiments using SEAL 
### Author: Ridha Alkhabaz 

Here, we are going to do some of the 

In [18]:
import argparse
import time
import os, sys
import torch
import pdb
import copy as cp
import numpy as np
import os.path as osp
import scipy.sparse as ssp
import torch.nn.functional as F
import torch_geometric.transforms as T
from tqdm import tqdm
from shutil import copy
from torch.nn import BCEWithLogitsLoss
from torch.utils.data import DataLoader
from torch_sparse import coalesce
from sklearn.metrics import roc_auc_score
from torch_geometric.datasets import FB15k_237
from torch_geometric.data import Data, Dataset, InMemoryDataset, DataLoader
from torch_geometric.utils import to_networkx, to_undirected
from torch_geometric.datasets import RelLinkPredDataset
from utils import *
from torch.nn import (ModuleList, Linear, Conv1d, MaxPool1d, Embedding, ReLU, 
                      Sequential, BatchNorm1d as BN)
from torch_geometric.nn import (GCNConv, SAGEConv, GINConv, 
                                global_sort_pool, global_add_pool, global_mean_pool)
device = torch.device('cuda' if torch.cuda.is_available() else 'cpu')
import warnings
warnings.filterwarnings("ignore")

In [3]:
# helpful funcstions and classes 
# this is for model definition and other things 
class DGCNN(torch.nn.Module):
    def __init__(self, hidden_channels, num_layers, max_z, k=0.6, train_dataset=None, 
                 dynamic_train=False, GNN=GCNConv, use_feature=False, 
                 node_embedding=None):
        super(DGCNN, self).__init__()

        self.use_feature = use_feature
        self.node_embedding = node_embedding

        if k <= 1:  # Transform percentile to number.
            if train_dataset is None:
                k = 30
            else:
                if dynamic_train:
                    sampled_train = train_dataset[:1000]
                else:
                    sampled_train = train_dataset
                num_nodes = sorted([g.num_nodes for g in sampled_train])
                k = num_nodes[int(math.ceil(k * len(num_nodes))) - 1]
                k = max(10, k)
        self.k = int(k)

        self.max_z = max_z
        self.z_embedding = Embedding(self.max_z, hidden_channels)

        self.convs = ModuleList()
        initial_channels = hidden_channels
        if self.use_feature:
            initial_channels += train_dataset.num_features
        if self.node_embedding is not None:
            initial_channels += node_embedding.embedding_dim

        self.convs.append(GNN(initial_channels, hidden_channels))
        for i in range(0, num_layers-1):
            self.convs.append(GNN(hidden_channels, hidden_channels))
        self.convs.append(GNN(hidden_channels, 1))

        conv1d_channels = [16, 32]
        total_latent_dim = hidden_channels * num_layers + 1
        conv1d_kws = [total_latent_dim, 5]
        self.conv1 = Conv1d(1, conv1d_channels[0], conv1d_kws[0],
                            conv1d_kws[0])
        self.maxpool1d = MaxPool1d(2, 2)
        self.conv2 = Conv1d(conv1d_channels[0], conv1d_channels[1],
                            conv1d_kws[1], 1)
        dense_dim = int((self.k - 2) / 2 + 1)
        dense_dim = (dense_dim - conv1d_kws[1] + 1) * conv1d_channels[1]
        self.lin1 = Linear(dense_dim, 128)
        self.lin2 = Linear(128, 1)

    def forward(self, z, edge_index, batch, x=None, edge_weight=None, node_id=None):
        z_emb = self.z_embedding(z)
        if z_emb.ndim == 3:  # in case z has multiple integer labels
            z_emb = z_emb.sum(dim=1)
        if self.use_feature and x is not None:
            x = torch.cat([z_emb, x.to(torch.float)], 1)
        else:
            x = z_emb
        if self.node_embedding is not None and node_id is not None:
            n_emb = self.node_embedding(node_id)
            x = torch.cat([x, n_emb], 1)
        xs = [x]

        for conv in self.convs:
            xs += [torch.tanh(conv(xs[-1], edge_index, edge_weight))]
        x = torch.cat(xs[1:], dim=-1)

        # Global pooling.
        x = global_sort_pool(x, batch, self.k)
        x = x.unsqueeze(1)  # [num_graphs, 1, k * hidden]
        x = F.relu(self.conv1(x))
        x = self.maxpool1d(x)
        x = F.relu(self.conv2(x))
        x = x.view(x.size(0), -1)  # [num_graphs, dense_dim]

        # MLP.
        x = F.relu(self.lin1(x))
        x = F.dropout(x, p=0.5, training=self.training)
        x = self.lin2(x)
        return x
# this is for dataset definition
class SEALDataset(InMemoryDataset):
    def __init__(self, root, data, split_edge, num_hops, percent=100, split='train', 
                 use_coalesce=False, node_label='drnl', ratio_per_hop=1.0, 
                 max_nodes_per_hop=None, directed=False):
        self.data = data
        self.split_edge = split_edge
        self.num_hops = num_hops
        self.percent = int(percent) if percent >= 1.0 else percent
        self.split = split
        self.use_coalesce = use_coalesce
        self.node_label = node_label
        self.ratio_per_hop = ratio_per_hop
        self.max_nodes_per_hop = max_nodes_per_hop
        self.directed = directed
        super(SEALDataset, self).__init__(root)
        self.data, self.slices = torch.load(self.processed_paths[0])

    @property
    def processed_file_names(self):
        if self.percent == 100:
            name = 'SEAL_{}_data'.format(self.split)
        else:
            name = 'SEAL_{}_data_{}'.format(self.split, self.percent)
        name += '.pt'
        return [name]

    def process(self):
        pos_edge, neg_edge = get_pos_neg_edges(self.split, self.split_edge, 
                                               self.data.edge_index, 
                                               self.data.num_nodes, 
                                               self.percent)

        if self.use_coalesce:  # compress mutli-edge into edge with weight
            self.data.edge_index, self.data.edge_weight = coalesce(
                self.data.edge_index, self.data.edge_weight, 
                self.data.num_nodes, self.data.num_nodes)

        if 'edge_weight' in self.data:
            edge_weight = self.data.edge_weight.view(-1)
        else:
            edge_weight = torch.ones(self.data.edge_index.size(1), dtype=int)
        A = ssp.csr_matrix(
            (edge_weight, (self.data.edge_index[0], self.data.edge_index[1])), 
            shape=(self.data.num_nodes, self.data.num_nodes)
        )

        if self.directed:
            A_csc = A.tocsc()
        else:
            A_csc = None
        
        # Extract enclosing subgraphs for pos and neg edges
        pos_list = extract_enclosing_subgraphs(
            pos_edge, A, self.data.x, 1, self.num_hops, self.node_label, 
            self.ratio_per_hop, self.max_nodes_per_hop, self.directed, A_csc)
        neg_list = extract_enclosing_subgraphs(
            neg_edge, A, self.data.x, 0, self.num_hops, self.node_label, 
            self.ratio_per_hop, self.max_nodes_per_hop, self.directed, A_csc)

        torch.save(self.collate(pos_list + neg_list), self.processed_paths[0])
        del pos_list, neg_list
def train():
    model.train()

    total_loss = 0
    pbar = tqdm(train_loader, ncols=70)
    for data in pbar:
        data = data.to(device)
        optimizer.zero_grad()
        x =  None
        edge_weight = None
        node_id = data.node_id if emb else None
        logits = model(data.z, data.edge_index, data.batch, x, edge_weight, node_id)
        loss = BCEWithLogitsLoss()(logits.view(-1), data.y.to(torch.float))
        loss.backward()
        optimizer.step()
        total_loss += loss.item() * data.num_graphs

    return total_loss / len(train_dataset)
@torch.no_grad()
def test():
    model.eval()

    y_pred, y_true = [], []
    for data in tqdm(val_loader, ncols=70):
        data = data.to(device)
        x =  None
        edge_weight = None
        node_id = data.node_id if emb else None
        logits = model(data.z, data.edge_index, data.batch, x, edge_weight, node_id)
        y_pred.append(logits.view(-1).cpu())
        y_true.append(data.y.view(-1).cpu().to(torch.float))
    val_pred, val_true = torch.cat(y_pred), torch.cat(y_true)
    pos_val_pred = val_pred[val_true==1]
    neg_val_pred = val_pred[val_true==0]

    y_pred, y_true = [], []
    for data in tqdm(test_loader, ncols=70):
        data = data.to(device)
        x =  None
        edge_weight =  None
        node_id = data.node_id if emb else None
        logits = model(data.z, data.edge_index, data.batch, x, edge_weight, node_id)
        y_pred.append(logits.view(-1).cpu())
        y_true.append(data.y.view(-1).cpu().to(torch.float))
    test_pred, test_true = torch.cat(y_pred), torch.cat(y_true)
    pos_test_pred = test_pred[test_true==1]
    neg_test_pred = test_pred[test_true==0]
    
   
    results = evaluate_mrr(val_pred, val_true, test_pred, test_true)

    return results
def evaluate_mrr(pos_val_pred, neg_val_pred, pos_test_pred, neg_test_pred):
    pos_val_pred = pos_val_pred.view(-1, 1)
    neg_val_pred = neg_val_pred.view(-1, 1)
    pos_test_pred = pos_test_pred.view(-1, 1)
    neg_test_pred = neg_test_pred.view(-1, 1)
    optimistic_rank_test = (neg_test_pred > pos_test_pred).sum(dim=1)
    optimistic_rank_val = (neg_val_pred > pos_val_pred).sum(dim=1)
    pessimistic_rank_test = (neg_test_pred >= pos_test_pred).sum(dim=1)
    pessimistic_rank_val = (neg_val_pred >= pos_val_pred).sum(dim=1)
    ranking_list_test = 0.5 * (optimistic_rank_test + pessimistic_rank_test) + 1
    ranking_list_val = 0.5 * (optimistic_rank_val + pessimistic_rank_val) + 1

    results = {}
    valid_mrr =  (1./ranking_list_val.to(torch.float)).mean()
    test_mrr = (1./ranking_list_test.to(torch.float)).mean()
   
    results['MRR'] = (valid_mrr, test_mrr)
    return results

In [21]:
dataset = RelLinkPredDataset('./rdata', 'FB15k-237')
data = dataset[0]
path = dataset.root 
split_edge = do_edge_split(dataset)
data.edge_index = split_edge['train']['edge'].t()
train_dataset = eval('SEALDataset')(
    path, 
    data, 
    split_edge, 
    num_hops=1, 
    percent=100, 
    split='train', 
    use_coalesce=False, 
    node_label='drnl', 
    ratio_per_hop=1.0, 
    max_nodes_per_hop=None, 
    directed=True, 
)
val_dataset = eval('SEALDataset')(
    path, 
    data, 
    split_edge, 
    num_hops=1, 
    percent=100, 
    split='valid', 
    use_coalesce=False, 
    node_label='drnl', 
    ratio_per_hop=1.0, 
    max_nodes_per_hop=None, 
    directed=True, 
) 
test_dataset = eval('SEALDataset')(
    path, 
    data, 
    split_edge, 
    num_hops=1, 
    percent=100, 
    split='test', 
    use_coalesce=False, 
    node_label='drnl', 
    ratio_per_hop=1.0, 
    max_nodes_per_hop=None, 
    directed=True, 
)  

Processing...
100%|██████████████████████████████████| 369754/369754 [07:22<00:00, 836.21it/s]
Done!
Processing...
100%|████████████████████████████████████| 13524/13524 [00:16<00:00, 830.07it/s]
Done!
Processing...
100%|████████████████████████████████████| 27049/27049 [00:32<00:00, 830.89it/s]
Done!


In [30]:
max_z = 1000 
train_loader = DataLoader(train_dataset, batch_size=32, 
                          shuffle=True, num_workers=0)
val_loader = DataLoader(val_dataset, batch_size=32, 
                           num_workers=0)
test_loader = DataLoader(test_dataset, batch_size=32, 
                           num_workers=0)
model = DGCNN(hidden_channels=32, num_layers=3, max_z=max_z, k=0.6, 
                      train_dataset=train_dataset, use_feature=None, 
                      node_embedding=None).to(device)

In [31]:
parameters = list(model.parameters())
optimizer = torch.optim.Adam(params=parameters, lr=0.0001)
total_params = sum(p.numel() for param in parameters for p in param)
print(f'Total number of parameters is {total_params}')

Total number of parameters is 178882


In [ ]:
emb = None
start_epoch = 1
loggers = {}
run = 1
for epoch in range(start_epoch, start_epoch + 30):
        loss = train()

        if epoch % 5 == 0:
            results = test()
            # for key, result in results.items():
            #     loggers[key].add_result(run, result)

            # if epoch % 1 == 0:
                # model_name = os.path.join(
                #     args.res_dir, 'run{}_model_checkpoint{}.pth'.format(run+1, epoch))
                # optimizer_name = os.path.join(
                #     args.res_dir, 'run{}_optimizer_checkpoint{}.pth'.format(run+1, epoch))
                # torch.save(model.state_dict(), model_name)
                # torch.save(optimizer.state_dict(), optimizer_name)

            for key, result in results.items():
                valid_res, test_res = result
                to_print = (f'Run: {run + 1:02d}, Epoch: {epoch:02d}, ' +
                            f'Loss: {loss:.4f}, Valid: {100 * valid_res:.2f}%, ' +
                            f'Test: {100 * test_res:.2f}%')
                print(key)
                print(to_print)
                    # with open(log_file, 'a') as f:
                    #     print(key, file=f)
                    #     print(to_print, file=f)

  0%|                                       | 0/23110 [00:00<?, ?it/s]/Users/ridhaalkhabaz/opt/anaconda3/envs/motif-disc/lib/python3.9/site-packages/torch_geometric/deprecation.py:22: UserWarning: 'nn.glob.global_sort_pool' is deprecated, use 'nn.aggr.SortAggr' instead
  warnings.warn(out)
  0%|                             | 2/23110 [00:00<1:04:51,  5.94it/s]

Intel MKL WARNING: Support of Intel(R) Streaming SIMD Extensions 4.2 (Intel(R) SSE4.2) enabled only processors has been deprecated. Intel oneAPI Math Kernel Library 2025.0 will require Intel(R) Advanced Vector Extensions (Intel(R) AVX) instructions.
Intel MKL WARNING: Support of Intel(R) Streaming SIMD Extensions 4.2 (Intel(R) SSE4.2) enabled only processors has been deprecated. Intel oneAPI Math Kernel Library 2025.0 will require Intel(R) Advanced Vector Extensions (Intel(R) AVX) instructions.


  0%|                               | 3/23110 [00:00<52:56,  7.27it/s]

Intel MKL WARNING: Support of Intel(R) Streaming SIMD Extensions 4.2 (Intel(R) SSE4.2) enabled only processors has been deprecated. Intel oneAPI Math Kernel Library 2025.0 will require Intel(R) Advanced Vector Extensions (Intel(R) AVX) instructions.
Intel MKL WARNING: Support of Intel(R) Streaming SIMD Extensions 4.2 (Intel(R) SSE4.2) enabled only processors has been deprecated. Intel oneAPI Math Kernel Library 2025.0 will require Intel(R) Advanced Vector Extensions (Intel(R) AVX) instructions.


  0%|                               | 5/23110 [00:00<45:19,  8.50it/s]

...

  8%|██▏                         | 1804/23110 [02:39<36:42,  9.67it/s]

Intel MKL WARNING: Support of Intel(R) Streaming SIMD Extensions 4.2 (Intel(R) SSE4.2) enabled only processors has been deprecated. Intel oneAPI Math Kernel Library 2025.0 will require Intel(R) Advanced Vector Extensions (Intel(R) AVX) instructions.
Intel MKL WARNING: Support of Intel(R) Streaming SIMD Extensions 4.2 (Intel(R) SSE4.2) enabled only processors has been deprecated. Intel oneAPI Math Kernel Library 2025.0 will require Intel(R) Advanced Vector Extensions (Intel(R) AVX) instructions.


  8%|██▏                         | 1806/23110 [02:39<31:54, 11.13it/s]

Intel MKL WARNING: Support of Intel(R) Streaming SIMD Extensions 4.2 (Intel(R) SSE4.2) enabled only processors has been deprecated. Intel oneAPI Math Kernel Library 2025.0 will require Intel(R) Advanced Vector Extensions (Intel(R) AVX) instructions.
Intel MKL WARNING: Support of Intel(R) Streaming SIMD Extensions 4.2 (Intel(R) SSE4.2) enabled only processors has been deprecated. Intel oneAPI Math Kernel Library 2025.0 will require Intel(R) Advanced Vector Extensions (Intel(R) AVX) instructions.
Intel MKL WARNING: Support of Intel(R) Streaming SIMD Extensions 4.2 (Intel(R) SSE4.2) enabled only processors has been deprecated. Intel oneAPI Math Kernel Library 2025.0 will require Intel(R) Advanced Vector Extensions (Intel(R) AVX) instructions.
Intel MKL WARNING: Support of Intel(R) Streaming SIMD Extensions 4.2 (Intel(R) SSE4.2) enabled only processors has been deprecated. Intel oneAPI Math Kernel Library 2025.0 will require Intel(R) Advanced Vector Extensions (Intel(R) AVX) instructions.


  8%|██▏                         | 1810/23110 [02:39<30:29, 11.64it/s]